# Running hyperparameter optimization on Chemprop model using RayTune

[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/chemprop/chemprop/blob/main/examples/hpopting.ipynb)

In [1]:
# Install chemprop from GitHub if running in Google Colab
import os

if os.getenv("COLAB_RELEASE_TAG"):
    try:
        import chemprop
    except ImportError:
        !git clone https://github.com/chemprop/chemprop.git
        %cd chemprop
        !pip install ".[hpopt]"
        %cd examples

## Import packages

In [2]:
from pathlib import Path
import sys

import pandas as pd
from lightning import pytorch as pl
import numpy as np
import ray
from ray import tune
from ray.train import CheckpointConfig, RunConfig, ScalingConfig
from ray.train.lightning import (RayDDPStrategy, RayLightningEnvironment,
                                 RayTrainReportCallback, prepare_trainer)
from ray.train.torch import TorchTrainer
from ray.tune.search.hyperopt import HyperOptSearch
from ray.tune.search.optuna import OptunaSearch
from ray.tune.schedulers import FIFOScheduler
import torch

from chemprop import data, featurizers, models, nn

# sys.path.insert(0, '../agenticadmet')
# from raytune_extra import RayTrainReportCallback

In [3]:
RANDOM_SEED = 42
np.random.seed(RANDOM_SEED)
torch.manual_seed(RANDOM_SEED)
torch.cuda.manual_seed_all(RANDOM_SEED)
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False

In [4]:
input_path = Path('../data/asap/datasets/rnd_splits/split_0.csv')
num_workers = 0 # number of workers for dataloader. 0 means using main process for data loading
smiles_column = 'smiles_std' # name of the column containing SMILES strings
target_columns = ['LogHLM', 'LogMLM', 'LogD', 'LogKSOL', 'LogMDR1-MDCKII'] # list of names of the columns containing targets

hpopt_save_dir = Path('../output/asap/rnd_splits/chemprop/run_0/split_0/hpopt') # directory to save hyperopt results
hpopt_save_dir.mkdir(exist_ok=True)

## Load data

In [5]:
df_input = pd.read_csv(input_path)
df_input

smiles    HLM   KSOL  LogD  \
0    COC1=CC=CC(Cl)=C1NC(=O)N1CCC[C@H](C(N)=O)C1 |a...    NaN    NaN   0.3   
1    O=C(NCC(F)F)[C@H](NC1=CC2=C(C=C1Br)CNC2)C1=CC(...    NaN  333.0   2.9   
2    O=C(NCC(F)F)[C@H](NC1=CC=C2CNCC2=C1)C1=CC(Br)=...    NaN    NaN   0.4   
3    NC(=O)[C@H]1CCCN(C(=O)CC2=CC=CC3=C2C=CO3)C1 |&...    NaN  376.0   1.0   
4     CC1=CC(CC(=O)N2CCC[C@H](C(N)=O)C2)=CC=N1 |&1:11|    NaN  375.0  -0.3   
..                                                 ...    ...    ...   ...   
399        CC(C)NC[C@H](O)COC1=CC=CC2=CC=CC=C12 |&1:5|   25.5    NaN   NaN   
400               O=C(O)CC1=CC=CC=C1NC1=C(Cl)C=CC=C1Cl  216.0    NaN   NaN   
401          NCC1=CC(Cl)=CC(C(=O)NC2=CC=C3CNCC3=C2)=C1    NaN    NaN   2.0   
402        COC(=O)NC1=NC2=CC=C(C(=O)C3=CC=CC=C3)C=C2N1    NaN    NaN   2.9   
403  CC1=NC=CN1C[C@H]1CCC2=C(C1=O)C1=CC=CC=C1N2C |&...    NaN  127.0   NaN   

       MLM  MDR1-MDCKII                                         smiles_std  \
0      NaN          2.0           COc1cccc(Cl)c1NC(=O)N1CCC[C@H](C(N)=O)C1   
1      NaN          0.2  O=C(NCC(F)F)[C@H](Nc1cc2c(cc1Br)CNC2)c1cc(Cl)c...   
2      NaN          0.5  O=C(NCC(F)F)[C@H](Nc1ccc2c(c1)CNC2)c1cc(Br)cc2...   
3      NaN          8.5            NC(=O)[C@H]1CCCN(C(=O)Cc2cccc3occc23)C1   
4      NaN          0.9              Cc1cc(CC(=O)N2CCC[C@H](C(N)=O)C2)ccn1   
..     ...          ...                                                ...   
399   63.0          NaN                    CC(C)NC[C@H](O)COc1cccc2ccccc12   
400  386.0          NaN                     O=C(O)Cc1ccccc1Nc1c(Cl)cccc1Cl   
401    NaN          NaN              NCc1cc(Cl)cc(C(=O)Nc2ccc3c(c2)CNC3)c1   
402    NaN          NaN            COC(=O)Nc1nc2ccc(C(=O)c3ccccc3)cc2[nH]1   
403    NaN          NaN              Cc1nccn1C[C@H]1CCc2c(c3ccccc3n2C)C1=O   

                                          cxsmiles_std  mol_idx smiles_ext  \
0      COc1cccc(Cl)c1NC(=O)N1CCC[C@H](C(N)=O)C1 |a:16|      191     |a:16|   
1    O=C(NCC(F)F)[C@H](Nc1cc2c(cc1Br)CNC2)c1cc(Cl)c...      335     |&1:7|   
2    O=C(NCC(F)F)[C@H](Nc1ccc2c(c1)CNC2)c1cc(Br)cc2...      336     |&1:7|   
3       NC(=O)[C@H]1CCCN(C(=O)Cc2cccc3occc23)C1 |&1:3|      300     |&1:3|   
4        Cc1cc(CC(=O)N2CCC[C@H](C(N)=O)C2)ccn1 |&1:11|      249    |&1:11|   
..                                                 ...      ...        ...   
399             CC(C)NC[C@H](O)COc1cccc2ccccc12 |&1:5|       22     |&1:5|   
400                     O=C(O)Cc1ccccc1Nc1c(Cl)cccc1Cl      380        NaN   
401              NCc1cc(Cl)cc(C(=O)Nc2ccc3c(c2)CNC3)c1      303        NaN   
402            COC(=O)Nc1nc2ccc(C(=O)c3ccccc3)cc2[nH]1      166        NaN   
403       Cc1nccn1C[C@H]1CCc2c(c3ccccc3n2C)C1=O |&1:7|      268     |&1:7|   

       LogHLM    LogMLM   LogKSOL  LogMDR1-MDCKII  split  
0         NaN       NaN       NaN        0.477121    val  
1         NaN       NaN  2.523746        0.079181  train  
2         NaN       NaN       NaN        0.176091  train  
3         NaN       NaN  2.576341        0.977724  train  
4         NaN       NaN  2.575188        0.278754  train  
..        ...       ...       ...             ...    ...  
399  1.423246  1.806180       NaN             NaN    val  
400  2.336460  2.587711       NaN             NaN    val  
401       NaN       NaN       NaN             NaN  train  
402       NaN       NaN       NaN             NaN  train  
403       NaN       NaN  2.107210             NaN  train  

[404 rows x 15 columns]

## Make data points, splits, and datasets

In [6]:
train_data, val_data = [], []
for _, row in df_input.iterrows():
    dp = data.MoleculeDatapoint.from_smi(row[smiles_column], row[target_columns].values)
    if row['split'] == 'train':
        train_data.append(dp)
    elif row['split'] == 'val':
        val_data.append(dp)

In [7]:
featurizer = featurizers.SimpleMoleculeMolGraphFeaturizer()

train_dset = data.MoleculeDataset(train_data, featurizer)
# scaler = train_dset.normalize_targets()

val_dset = data.MoleculeDataset(val_data, featurizer)
# val_dset.normalize_targets(scaler)

# Define helper function to train the model

In [8]:
# def train_model(config, train_dset, val_dset, num_workers, scaler):
def train_model(config, train_dset, val_dset, num_workers):
    # config is a dictionary containing hyperparameters used for the trial
    depth = int(config["depth"])
    ffn_hidden_dim = int(config["ffn_hidden_dim"])
    ffn_num_layers = int(config["ffn_num_layers"])
    message_hidden_dim = int(config["message_hidden_dim"])
    dropout = float(config["dropout"])

    train_loader = data.build_dataloader(train_dset, num_workers=num_workers, shuffle=True)
    val_loader = data.build_dataloader(val_dset, num_workers=num_workers, shuffle=False)

    mp = nn.BondMessagePassing(d_h=message_hidden_dim, depth=depth, dropout=dropout)
    agg = nn.MeanAggregation()
    # output_transform = nn.UnscaleTransform.from_standard_scaler(scaler)
    # ffn = nn.RegressionFFN(output_transform=output_transform, input_dim=message_hidden_dim, hidden_dim=ffn_hidden_dim, n_layers=ffn_num_layers)
    ffn = nn.RegressionFFN(
        n_tasks=len(target_columns),
        output_transform=None, input_dim=message_hidden_dim, hidden_dim=ffn_hidden_dim, n_layers=ffn_num_layers,
        dropout=dropout
    )
    batch_norm = True
    metric_list = [nn.metrics.MAE(), nn.metrics.R2Score()]
    model = models.MPNN(mp, agg, ffn, batch_norm, metric_list)

    trainer = pl.Trainer(
        accelerator="auto",
        devices=1,
        max_epochs=200, # number of epochs to train for
        # below are needed for Ray and Lightning integration
        strategy=RayDDPStrategy(),
        callbacks=[RayTrainReportCallback()],
        plugins=[RayLightningEnvironment()],
        enable_progress_bar=False,
        enable_checkpointing=False
    )

    trainer = prepare_trainer(trainer)
    trainer.fit(model, train_loader, val_loader)

## Define parameter search space

In [9]:
search_space = {
    "depth": tune.qrandint(lower=2, upper=6, q=1),
    "ffn_hidden_dim": tune.qrandint(lower=300, upper=2400, q=100),
    "ffn_num_layers": tune.qrandint(lower=1, upper=3, q=1),
    "message_hidden_dim": tune.qrandint(lower=300, upper=2400, q=100),
    "dropout": tune.uniform(0.0, 0.2)
}

In [10]:
ray.shutdown()
ray.init(include_dashboard=False)

scheduler = FIFOScheduler()

# Scaling config controls the resources used by Ray
scaling_config = ScalingConfig(
    num_workers=1,
    use_gpu=True, # set to True if you want to use GPU
)

# Checkpoint config controls the checkpointing behavior of Ray
checkpoint_config = CheckpointConfig(
    num_to_keep=1, # number of checkpoints to keep
    checkpoint_score_attribute="val_loss", # Save the checkpoint based on this metric
    checkpoint_score_order="min", # Save the checkpoint with the lowest metric value
    checkpoint_frequency=0,        # Do not checkpoint during training
)

run_config = RunConfig(
    checkpoint_config=checkpoint_config,
    storage_path=(hpopt_save_dir / "ray_results").absolute(), # directory to save the results
)

ray_trainer = TorchTrainer(
    lambda config: train_model(
        # config, train_dset, val_dset, num_workers, scaler
        config, train_dset, val_dset, num_workers
    ),
    scaling_config=scaling_config,
    run_config=run_config,
)

search_alg = HyperOptSearch(
    n_initial_points=10, # number of random evaluations before tree parzen estimators
    random_state_seed=RANDOM_SEED,
)

# OptunaSearch is another search algorithm that can be used
# search_alg = OptunaSearch()

tune_config = tune.TuneConfig(
    metric="val_loss",
    mode="min",
    num_samples=30, # number of trials to run
    scheduler=scheduler,
    search_alg=search_alg,
    trial_dirname_creator=lambda trial: str(trial.trial_id), # shorten filepaths
)

tuner = tune.Tuner(
    ray_trainer,
    param_space={
        "train_loop_config": search_space,
    },
    tune_config=tune_config,
)

# Start the hyperparameter search
results = tuner.fit()

(raylet) [2025-03-11 21:33:34,190 E 523488 523522] (raylet) file_system_monitor.cc:116: /var/tmp/ray/session_2025-03-11_21-33-22_789751_523270 is over 95% full, available space: 13.203 GB; capacity: 295.046 GB. Object creation will fail if spilling is required.
(TorchTrainer pid=524465) Started distributed worker processes: 
(TorchTrainer pid=524465) - (node_id=bacb29b8d065787f0e01b2822b0783aff180964574869eeacae5f33c, ip=10.128.0.3, pid=524734) world_rank=0, local_rank=0, node_rank=0
(RayTrainWorker pid=524734) Setting up process group for: env:// [rank=0, world_size=1]
(RayTrainWorker pid=524734) /opt/conda/envs/admet/lib/python3.11/site-packages/ray/train/lightning/_lightning_utils.py:262: This API is deprecated and may be removed in future Ray releases. You could suppress this warning by setting env variable PYTHONWARNINGS="ignore::DeprecationWarning"
(RayTrainWorker pid=524734) `get_trial_name` is deprecated because the concept of a `Trial` will soon be removed in Ray Train.Ray Tra

## Hyperparameter optimization results

In [11]:
# results of all trials
result_df = results.get_dataframe()
results_df = result_df.sort_values('val/mae')
results_df

train_loss  train_loss_step   val/mae    val/r2  val_loss  \
14    0.079665         0.099432  0.333156  0.778627  0.205901   
12    0.096029         0.292531  0.333983  0.787656  0.197503   
19    0.088536         0.118046  0.334023  0.790624  0.194742   
2     0.065592         0.185106  0.336174  0.771428  0.212597   
17    0.078883         0.247472  0.336263  0.784005  0.200899   
20    0.052391         0.146330  0.351267  0.757447  0.225600   
11    0.095477         0.182505  0.351294  0.761386  0.221937   
9     0.079465         0.122593  0.353521  0.749816  0.232698   
10    0.059563         0.220698  0.353864  0.770414  0.213539   
18    0.082483         0.206700  0.358206  0.751251  0.231363   
22    0.116963         0.189095  0.358318  0.756167  0.226791   
0     0.053512         0.164948  0.358812  0.752419  0.230277   
27    0.133009         0.249673  0.361569  0.757082  0.225940   
23    0.105445         0.314881  0.364717  0.754770  0.228091   
6     0.124914         0.191656  0.365408  0.748694  0.233742   
26    0.137602         0.125560  0.365967  0.752040  0.230630   
5     0.073522         0.162442  0.371128  0.736995  0.244623   
1     0.155736         0.263326  0.373290  0.740394  0.241461   
7     0.081500         0.130444  0.373345  0.730577  0.250593   
24    0.103290         0.299232  0.374155  0.742704  0.239313   
16    0.117085         0.185482  0.376865  0.731019  0.250182   
28    0.132797         0.201461  0.383976  0.719780  0.260635   
3     0.110752         0.304377  0.386981  0.715128  0.264962   
15    0.152945         0.304236  0.389983  0.693657  0.284932   
29    0.199079         0.175825  0.391787  0.696276  0.282497   
21    0.110517         0.119106  0.391807  0.719206  0.261169   
13    0.105037         0.181339  0.392361  0.700285  0.278768   
8     0.094774         0.280282  0.402029  0.703812  0.275487   
4     0.152651         0.243850  0.406797  0.694082  0.284537   
25    0.172157         0.282075  0.416446  0.662861  0.313576   

    train_loss_epoch  epoch  step   timestamp checkpoint_dir_name  ...  \
14          0.079665    199  1200  1741731889   checkpoint_000199  ...   
12          0.096029    199  1200  1741731513   checkpoint_000199  ...   
19          0.088536    199  1200  1741733177   checkpoint_000199  ...   
2           0.065592    199  1200  1741729324   checkpoint_000199  ...   
17          0.078883    199  1200  1741732716   checkpoint_000199  ...   
20          0.052391    199  1200  1741733322   checkpoint_000199  ...   
11          0.095477    199  1200  1741731406   checkpoint_000199  ...   
9           0.079465    199  1200  1741731132   checkpoint_000199  ...   
10          0.059563    199  1200  1741731251   checkpoint_000199  ...   
18          0.082483    199  1200  1741732918   checkpoint_000199  ...   
22          0.116963    199  1200  1741733904   checkpoint_000199  ...   
0           0.053512    199  1200  1741728962   checkpoint_000199  ...   
27          0.133009    199  1200  1741735642   checkpoint_000199  ...   
23          0.105445    199  1200  1741734170   checkpoint_000199  ...   
6           0.124914    199  1200  1741730332   checkpoint_000199  ...   
26          0.137602    199  1200  1741735453   checkpoint_000199  ...   
5           0.073522    199  1200  1741730086   checkpoint_000199  ...   
1           0.155736    199  1200  1741729224   checkpoint_000199  ...   
7           0.081500    199  1200  1741730733   checkpoint_000199  ...   
24          0.103290    199  1200  1741734511   checkpoint_000199  ...   
16          0.117085    199  1200  1741732529   checkpoint_000199  ...   
28          0.132797    199  1200  1741735918   checkpoint_000199  ...   
3           0.110752    199  1200  1741729646   checkpoint_000199  ...   
15          0.152945    199  1200  1741732362   checkpoint_000199  ...   
29          0.199079    199  1200  1741736328   checkpoint_000199  ...   
21          0.110517    199  1200  1741733645   checkpoint_00019

In [12]:
results_df.to_csv(hpopt_save_dir / 'results.csv', index=False)

In [13]:
ray.shutdown()